# Random Forest: Hyperparameter Tuning, Feature Selection, Training

In [1]:
import pandas as pd
import numpy as np
import sklearn as sk
import gc
import seaborn as sns
import matplotlib.pyplot as plt
import re
import optuna
import joblib

from utils import split_time_series
from sklearn.preprocessing import MinMaxScaler

from optuna.visualization import plot_parallel_coordinate
from optuna.visualization import plot_contour

pd.set_option('display.max_rows', 600)
pd.set_option('display.max_columns', 50)


In [2]:
print("hi")

hi


In [3]:
# Read data from the preprocessed data
data_sales = pd.read_pickle('data/data_sales_01.pickle')

- Drop the target label from training data
- Use dates to determine index of training/val/test split

In [4]:
drop_cols_fit = ["target"]
dates = data_sales['date_block_num']

In [5]:
test_idx = dates.max()
start_idx = 0
data_train = data_sales.loc[data_sales.date_block_num < 34, :]

In [6]:
data_train

date_block_num  shop_id  item_id  target  item_category_id  name2  \
0                      0        2       19     0.0                40      4   
1                      0        2       27     1.0                19     76   
2                      0        2       28     0.0                30    107   
3                      0        2       29     0.0                23    123   
4                      0        2       32     0.0                40      4   
...                  ...      ...      ...     ...               ...    ...   
10913799              33       59    22162     0.0                40      4   
10913800              33       59    22163     0.0                40      4   
10913801              33       59    22164     0.0                37      4   
10913802              33       59    22166     0.0                54    171   
10913803              33       59    22167     0.0                49      4   

          name3  city  type  subtype  target_lag_1  target_lag_2  \
0            42     0    11        4           NaN           NaN   
1            42     0     5       10           NaN           NaN   
2            42     0     8       55           NaN           NaN   
3            42     0     5       16           NaN           NaN   
4            42     0    11        4           NaN           NaN   
...         ...   ...   ...      ...           ...           ...   
10913799     42    30    11        4           0.0           1.0   
10913800     36    30    11        4           0.0           0.0   
10913801    562    30    11        1           0.0           0.0   
10913802     42    30    12       61           0.0           0.0   
10913803     19    30    12       39           0.0           0.0   

          target_lag_3  target_lag_6  target_lag_12  target_mean_month_lag_1  \
0                  NaN           NaN            NaN                      NaN   
1                  NaN           NaN            NaN                      NaN   
2                  NaN           NaN            NaN                      NaN   
3                  NaN           NaN            NaN                      NaN   
4                  NaN           NaN            NaN                      NaN   
...                ...           ...            ...                      ...   
10913799           0.0           1.0            NaN                 0.263758   
10913800           NaN           NaN            NaN                 0.263758   
10913801           1.0           2.0            NaN                 0.263758   
10913802           0.0           0.0            0.0                 0.263758   
10913803           0.0           0.0            0.0                 0.263758   

          target_mean_month_lag_2  target_mean_month_lag_3  \
0                             NaN                      NaN   
1                             NaN                      NaN   
2                             NaN                      NaN   
3                             NaN                      NaN   
4                             NaN                      NaN   
...                           ...                      ...   
10913799                 0.287989                  0.25923   
10913800                 0.287989                      NaN   
10913801                 0.287989                  0.25923   
10913802                 0.287989                  0.25923   
10913803                 0.287989                  0.25923   

          target_mean_month_lag_6  target_mean_month_lag_12  \
0                             NaN                       NaN   
1                             NaN                       NaN   
2                             NaN                       NaN   
3                             NaN                       NaN   
4                             NaN                       NaN   
...                           ...                       ...   
10913799                 0.243033                       NaN   
10913800                      NaN 

Before moving on, we need to impute missing values since Randomforest from sklearn does not have algorithm to deal with them, unlike XGBoost.
This can be achieved in several ways such filling with meadian/mean/mode or KNN imputing. I tried KNN imputing by changin distance metric to accomodate categorical distances
using KNN imputing of sklearn. The relevant code for this could be found in utils.py. But, the current implementation is not really fast, takes long for a large data set since it calculates
neighbors in units of memory chunks, to avoid memory overload due to space complexity $O(N^2)$ of generic computing pairwise distance matrix.

Then, I continued with filling it with median or -100 (a value distinct from other values in the data). Since median imputing gave better results, I continued with median filling.

In [7]:
data_sales.fillna(data_sales.median(), inplace=True)

In [8]:
data_sales.isna().sum() / data_sales.shape[0]

date_block_num                 0.0
shop_id                        0.0
item_id                        0.0
target                         0.0
item_category_id               0.0
name2                          0.0
name3                          0.0
city                           0.0
type                           0.0
subtype                        0.0
target_lag_1                   0.0
target_lag_2                   0.0
target_lag_3                   0.0
target_lag_6                   0.0
target_lag_12                  0.0
target_mean_month_lag_1        0.0
target_mean_month_lag_2        0.0
target_mean_month_lag_3        0.0
target_mean_month_lag_6        0.0
target_mean_month_lag_12       0.0
target_shop_mean_lag_1         0.0
target_shop_mean_lag_2         0.0
target_shop_mean_lag_3         0.0
target_shop_mean_lag_12        0.0
target_category_mean_lag_1     0.0
target_category_mean_lag_2     0.0
target_category_mean_lag_3     0.0
target_category_mean_lag_12    0.0
target_item_mean_lag

In [12]:
from sklearn.metrics import mean_squared_error
from sklearn.ensemble import RandomForestRegressor

# Values of the hyperparameters to be searched
search_space = {
    'n_estimators': [140],
    'max_depth': [17],
    'max_features': ['sqrt'],
    'max_samples':[0.5, 0.75], 
}


def objective_hyperparam(trial):

    # Dictionary to map from parameter name to values
    params = {
        'n_estimators': trial.suggest_int("n_estimators", 1, 301),
        'max_depth': trial.suggest_int("max_depth", 1, 120, step=1),
        'max_features': trial.suggest_categorical("max_features", ['auto', 'sqrt']),
        'eval_metric': ['rmse'],
        'max_samples':trial.suggest_float("max_samples", 0.5, 0.9, step=0.01), 
        'seed': 42,
        'verbose' : False,
    }
    
    model = RandomForestRegressor(
                    n_estimators = params['n_estimators'],
                    max_depth = params['max_depth'],
                    max_features = params['max_features'],
                    max_samples = params['max_samples'],
                    random_state = params['seed'],
                    n_jobs=4,
                    )
    
    split_num = 3
    total_score = 0

    # Calculate score of model by taking weighted average over 5 splits
    for i in range(split_num):
        # print(10*"*" + f"This is split {i}"+10*"*")
        val_idx = dates.max() - (i+1)
        start_idx = val_idx - 24
        X_train, X_val, y_train, y_val = split_time_series(data_sales, val_idx, drop_cols_fit, start_idx)
        # print((X_train.shape, X_val.shape, y_train.shape, y_val.shape))
        
        # Apply min-max normalization
        scaler = MinMaxScaler().fit(X_train)
        X_train = scaler.transform(X_train)
        X_val = scaler.transform(X_val)

        model.fit(X_train, y_train)


        # Predictions
        yhat_val = model.predict(X_val).clip(0,20)

        # RMSE for the predictions
        rmse = mean_squared_error(yhat_val, y_val, squared=False)
        
        total_score += rmse*(split_num-i)
    
    # Take the averegge
    total_score = total_score / (split_num*(split_num+1)/2)
    
    return total_score

In [17]:
# Study object to optimize objective_hyperparam function
study = optuna.create_study(sampler=optuna.samplers.GridSampler(search_space))
study.add_trials(joblib.load("data/study_bagging_00.pkl").trials)


[I 2022-03-29 06:59:30,688] A new study created in memory with name: no-name-52fff880-4a79-4b21-978b-109b09644e4b
/tmp/ipykernel_6368/3060926382.py:3: ExperimentalWarning: add_trials is experimental (supported from v2.5.0). The interface can change in the future.
  study.add_trials(joblib.load("data/study_bagging_00.pkl").trials)
/home/ubuntu/miniconda3/lib/python3.9/site-packages/optuna/study/study.py:969: ExperimentalWarning: add_trial is experimental (supported from v2.0.0). The interface can change in the future.
  self.add_trial(trial)


In [18]:
study.trials_dataframe()

number     value             datetime_start          datetime_complete  \
0        0  0.912852 2022-03-26 12:10:22.516684 2022-03-26 12:50:10.888872   
1        1  0.912885 2022-03-26 12:50:10.890257 2022-03-26 13:22:57.867842   
2        2  0.901057 2022-03-26 13:36:16.808435 2022-03-26 14:20:51.485119   
3        3  0.900386 2022-03-26 14:20:51.486467 2022-03-26 15:00:50.254539   
4        4  0.891141 2022-03-26 17:03:08.662163 2022-03-26 17:57:11.524981   
5        5  0.891594 2022-03-26 17:57:11.528064 2022-03-26 18:43:12.063682   
6        6  0.884484 2022-03-27 01:10:16.757826 2022-03-27 01:33:05.122077   
7        7  0.882718 2022-03-27 01:33:05.123459 2022-03-27 01:50:37.761037   
8        8  0.879029 2022-03-27 02:01:17.781329 2022-03-27 02:26:11.544806   
9        9  0.880596 2022-03-27 02:26:11.546166 2022-03-27 02:50:15.930809   
10      10  0.912302 2022-03-27 07:30:08.827635 2022-03-27 07:51:19.709661   
11      11  0.912732 2022-03-27 07:51:19.711003 2022-03-27 08:07:30.388483   
12      12  0.900290 2022-03-27 08:10:22.509729 2022-03-27 08:55:05.340612   
13      13  0.899622 2022-03-27 08:55:05.341961 2022-03-27 09:50:32.299236   
14      14  0.890755 2022-03-27 17:16:48.657246 2022-03-27 18:13:41.416866   
15      15  0.890390 2022-03-27 18:28:06.552697 2022-03-27 19:44:14.896820   
16      16  0.882613 2022-03-28 19:44:29.604896 2022-03-28 20:12:33.117072   
17      17  0.883906 2022-03-28 20:14:01.562303 2022-03-28 21:30:38.772499   
18      18  0.878758 2022-03-29 05:46:56.690349 2022-03-29 06:26:30.430729   
19      19  0.880954 2022-03-29 06:26:30.433862 2022-03-29 06:55:55.851348   

                 duration  params_max_depth params_max_features  \
0  0 days 00:39:48.372188                 9                sqrt   
1  0 days 00:32:46.977585                 9                sqrt   
2  0 days 00:44:34.676684                11                sqrt   
3  0 days 00:39:58.768072                11                sqrt   
4  0 days 00:54:02.862818                13                sqrt   
5  0 days 00:46:00.535618                13                sqrt   
6  0 days 00:22:48.364251                15                sqrt   
7  0 days 00:17:32.637578                15                sqrt   
8  0 days 00:24:53.763477                17                sqrt   
9  0 days 00:24:04.384643                17                sqrt   
10 0 days 00:21:10.882026                 9                sqrt   
11 0 days 00:16:10.677480                 9                sqrt   
12 0 days 00:44:42.830883                11                sqrt   
13 0 days 00:55:26.957275                11                sqrt   
14 0 days 00:56:52.759620                13                sqrt   
15 0 days 01:16:08.344123                13                sqrt   
16 0 days 00:28:03.512176                15                sqrt   
17 0 days 01:16:37.210196                15                sqrt   
18 0 days 00:39:33.740380                17                sqrt   
19 0 days 00:29:25.417486                17                sqrt   

    params_max_samples  params_n_estimators  system_attrs_grid_id  \
0                 0.75                  100                     1   
1                 0.50                  100                     0   
2                 0.75                  100                     1   
3                 0.50                  100                     0   
4                 0.75                  100                     1   
5                 0.50                  100                     0   
6                 0.75                  100                     1   
7                 0.50                  100                     0   
8                 0.75                  100                     1   
9                 0.50                  100                     0   
10                0.75                  140                     1   
11                0.50                  140                     0   
12                0.75                  140                 

In [15]:
study.optimize(objective_hyperparam)

[I 2022-03-29 06:26:30,431] Trial 18 finished with value: 0.8787583052143771 and parameters: {'n_estimators': 140, 'max_depth': 17, 'max_features': 'sqrt', 'max_samples': 0.75}. Best is trial 18 with value: 0.8787583052143771.
[I 2022-03-29 06:55:55,851] Trial 19 finished with value: 0.8809541370108057 and parameters: {'n_estimators': 140, 'max_depth': 17, 'max_features': 'sqrt', 'max_samples': 0.5}. Best is trial 18 with value: 0.8787583052143771.


In [16]:
# Store study object to disk
joblib.dump(study, "data/study_bagging_00.pkl")

['data/study_bagging_00.pkl']

In [38]:
joblib.load("data/study_bagging_00.pkl").trials

[FrozenTrial(number=0, values=[0.9128519491342053], datetime_start=datetime.datetime(2022, 3, 26, 12, 10, 22, 516684), datetime_complete=datetime.datetime(2022, 3, 26, 12, 50, 10, 888872), params={'n_estimators': 100, 'max_depth': 9, 'max_features': 'sqrt', 'max_samples': 0.75}, distributions={'n_estimators': IntUniformDistribution(high=301, low=1, step=1), 'max_depth': IntUniformDistribution(high=120, low=1, step=1), 'max_features': CategoricalDistribution(choices=('auto', 'sqrt')), 'max_samples': DiscreteUniformDistribution(high=0.9, low=0.5, q=0.01)}, user_attrs={}, system_attrs={'search_space': OrderedDict([('max_depth', [9]), ('max_features', ['sqrt']), ('max_samples', [0.5, 0.75]), ('n_estimators', [100])]), 'grid_id': 1}, intermediate_values={}, trial_id=0, state=TrialState.COMPLETE, value=None),
 FrozenTrial(number=1, values=[0.9128847827880877], datetime_start=datetime.datetime(2022, 3, 26, 12, 50, 10, 890257), datetime_complete=datetime.datetime(2022, 3, 26, 13, 22, 57, 86784

In [21]:
# Store study object to disk
joblib.dump(study, "data/study_bagging_00.pkl")

['data/study_bagging_00.pkl']

In [33]:
%whos

Variable                   Type         Data/Info
-------------------------------------------------
MinMaxScaler               type         <class 'sklearn.preproces<...>sing._data.MinMaxScaler'>
RandomForestRegressor      ABCMeta      <class 'sklearn.ensemble.<...>t.RandomForestRegressor'>
data_sales                 DataFrame              date_block_num <...>128004 rows x 38 columns]
data_train                 DataFrame              date_block_num <...>913804 rows x 38 columns]
dates                      Series       0            0\n1        <...>h: 11128004, dtype: int32
drop_cols_fit              list         n=1
gc                         module       <module 'gc' (built-in)>
joblib                     module       <module 'joblib' from '/h<...>ages/joblib/__init__.py'>
mean_squared_error         function     <function mean_squared_error at 0x7fb6fa0fd550>
np                         module       <module 'numpy' from '/ho<...>kages/numpy/__init__.py'>
objective_hyperparam       func

Having found the optimal hyperparameters, lets apply feature selection to see if we can easy computation. One simple way to do feature selection is to use Correlation matrix between features and label over training data

In [12]:
# Calculate correlation matrix
corr = data_train.corr() 

In [13]:
# Plot the correlation matrix
# Set figure size
plt.figure(figsize=(60,60), dpi=400)
sns.heatmap(corr, annot=True, cmap=plt.cm.PuBu)
plt.savefig("corr_RF.png")
plt.show()

To getter better features, in principle, we could eliminate the featues with very strong correlations since they would follow similar set of values for the same label, rendering them a bit useless for node splitting when constructing trees. But, I want to try better features selection methods since the data involves many complicated features and it is relatively big.

Indeed, there are few experimental results showing that we could better. I will try the other filter method based on univariate selection with f-test

In [15]:
# Get the absolute value of the correlation
cor_target = abs(cor["target"])

# Select highly correlated features (thresold = 0.2)
relevant_features = cor_target[cor_target>0.2]

In [ ]:
"""
.. _distributed:

Easy Parallelization
====================

It's straightforward to parallelize :func:`optuna.study.Study.optimize`.

If you want to manually execute Optuna optimization:

    1. start an RDB server (this example uses MySQL)
    2. create a study with `--storage` argument
    3. share the study among multiple nodes and processes

Of course, you can use Kubernetes as in `the kubernetes examples <https://github.com/optuna/optuna-examples/tree/main/kubernetes>`_.

To just see how parallel optimization works in Optuna, check the below video.

.. raw:: html

    <iframe width="560" height="315" src="https://www.youtube.com/embed/J_aymk4YXhg?start=427" frameborder="0" allow="accelerometer; autoplay; encrypted-media; gyroscope; picture-in-picture" allowfullscreen></iframe>


Create a Study
--------------

You can create a study using ``optuna create-study`` command.
Alternatively, in Python script you can use :func:`optuna.create_study`.


.. code-block:: bash

    $ mysql -u root -e "CREATE DATABASE IF NOT EXISTS example"
    $ optuna create-study --study-name "distributed-example" --storage "mysql://root@localhost/example"
    [I 2020-07-21 13:43:39,642] A new study created with name: distributed-example


Then, write an optimization script. Let's assume that ``foo.py`` contains the following code.

.. code-block:: python

    import optuna


    def objective(trial):
        x = trial.suggest_float("x", -10, 10)
        return (x - 2) ** 2


    if __name__ == "__main__":
        study = optuna.load_study(
            study_name="distributed-example", storage="mysql://root@localhost/example"
        )
        study.optimize(objective, n_trials=100)


Share the Study among Multiple Nodes and Processes
--------------------------------------------------

Finally, run the shared study from multiple processes.
For example, run ``Process 1`` in a terminal, and do ``Process 2`` in another one.
They get parameter suggestions based on shared trials' history.

Process 1:

.. code-block:: bash

    $ python foo.py
    [I 2020-07-21 13:45:02,973] Trial 0 finished with value: 45.35553104173011 and parameters: {'x': 8.73465151598285}. Best is trial 0 with value: 45.35553104173011.
    [I 2020-07-21 13:45:04,013] Trial 2 finished with value: 4.6002397305938905 and parameters: {'x': 4.144816945707463}. Best is trial 1 with value: 0.028194513284051464.
    ...

Process 2 (the same command as process 1):

.. code-block:: bash

    $ python foo.py
    [I 2020-07-21 13:45:03,748] Trial 1 finished with value: 0.028194513284051464 and parameters: {'x': 1.8320877810162361}. Best is trial 1 with value: 0.028194513284051464.
    [I 2020-07-21 13:45:05,783] Trial 3 finished with value: 24.45966755098074 and parameters: {'x': 6.945671597566982}. Best is trial 1 with value: 0.028194513284051464.
    ...

.. note::
    We do not recommend SQLite for distributed optimizations at scale because it may cause deadlocks and serious performance issues. Please consider to use another database engine like PostgreSQL or MySQL.

.. note::
    Please avoid putting the SQLite database on NFS when running distributed optimizations. See also: https://www.sqlite.org/faq.html#q5

"""